### An engineering problem from "Engineering Optimization" by Xin-She Yang

Goal: Design an optimal spring (cheapest / least material needed) that does the job. Parameters we can change: $d$, the diameter of the coil; $L$, the length of the spring; $w$, the thickness of the wire.

Task: Minimize $$(2+L)dw^2$$ subject to the constraints
\begin{align*}
g_1(L,d,w) &= 1 - \frac{d^3L}{7178w^4} \leq 0\\[5pt]
g_2(L,d,w) &= \frac{4d^2 - wd}{12566dw^3 - w^4} + \frac{1}{5108w^2} - 1 \leq 0\\[5pt]
g_3(L,d,w) &= 1 - \frac{140.45w}{d^2L} \leq 0\\[5pt]
g_4(L,d,w) &= \frac{w+d}{1.5} - 1 \leq 0
\end{align*}
with boundary conditions
$$
0.05 \leq w \leq 2.0
\qquad\qquad
0.25 \leq d \leq 1.3
\qquad\qquad
2.0 \leq L \leq 15.0
$$

In [1]:
import math
import random

In [2]:
def g1(L,d,w):
    return 1 - d**3 * L / (7178 * w**4)

def g2(L,d,w):
    return (4*d**2 - w*d)/(12566 * d * w**3 - w**4) + 1/(5108*w**2) - 1

def g3(L,d,w):
    return 1 - 140.45 * w / (d**2*L)

def g4(L,d,w):
    return (w+d)/1.5 - 1

def satisfies_constraints(L,d,w):
    return g1(L,d,w) <= 0 and g2(L,d,w) <= 0 and g3(L,d,w) <= 0 and g4(L,d,w) <= 0

In [3]:
satisfies_constraints(14.58629717, 0.07341016, 0.0299435)

False

In [ ]:
# satisfies_constraints(point[0], point[1], point[2])
# satisfies_constraints(*points)
# list unpacking

In [4]:
satisfies_constraints(*[14.58629717, 0.07341016, 0.0299435])

False

In [6]:
L, d, w = [14.58629717, 0.07341016, 0.0299435]
g1(L,d,w), g2(L,d,w), g3(L,d,w), g4(L,d,w)

(3.082522715969205e-07,
 -2.3389332648449113e-07,
 -52.5016168980595,
 -0.93109756)

In [7]:
def score(L,d,w):  # w-squared is "w**2" not "w^2"
    return (2+L)*d*w**2

In [8]:
def tweak(L,d,w):
    # new_w = old_w + a number between -delta_w and +delta_w

    delta_w = 0.01
    delta_d = 0.01
    delta_L = 0.1
    
    # checks boundary conditions only, not the other constraints
    new_w = w + random.uniform(-delta_w, delta_w)
    while new_w < 0.05 or new_w > 2:
        new_w = w + random.uniform(-delta_w, delta_w)
    
    new_d = d + random.uniform(-delta_d, delta_d)
    while new_d < 0.25 or new_d > 1.3:
        new_d = d + random.uniform(-delta_d, delta_d)
        
    new_L = L + random.uniform(-delta_L, delta_L)
    while new_L < 2 or new_L > 15:
        new_L = L + random.uniform(-delta_L, delta_L)
        
    return (new_L, new_d, new_w)
        
tweak(15, 1.3, 2.0)

(14.969796926434249, 1.297961745340554, 1.9972983358000478)

In [ ]:
def random_solution():
    return (
        random.uniform(2, 15),
        random.uniform(0.25, 1.3),
        random.uniform(0.05, 2),
    )
print(random_solution())

In [ ]:
def hill_climbing():
    
    start = random_solution()
    while not satisfies_constraints(*start):
        start = random_solution()
    sol = start
    value = score(*sol)

    bad = 0
    while True:
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)
        new_value = score(*new_sol)
        if new_value < value:
            bad = 0
            sol = new_sol
            value = new_value
            
        else:
            bad += 1
            if bad > 1000:
                return sol
    


In [ ]:
sol = hill_climbing()
print(sol)

print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))
print(score(*sol))

In [ ]:
# smarter: sample 1000 tweaks to find a good initial_temp that gives a desired p_0
# or: heat the system slowly until the % of worsening solutions is what you want
initial_temp = 0.005
alpha = 0.99
final_temp = initial_temp / 10000
trials_per_temp = 10000

start = random_solution()
while not satisfies_constraints(*start):
    start = random_solution()
sol = start
value = score(*sol)

In [ ]:
temp = initial_temp
generation = 0
best_sol = None
best_score = None

while temp >= final_temp:
    generation += 1
    accepted_worse = 0
    total_worse = 0
    for i in range(trials_per_temp):
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)

        new_value = score(*new_sol)
        
        delta = new_value - value
        delta *= -1
        if delta >= 0:
            sol = new_sol
            value = new_value
            if best_score is None or value < best_score:
                best_sol = sol
                best_score = value
        else:
            total_worse += 1
            p = math.exp(delta/temp)
            r = random.random()
            if r <= p:
                accepted_worse += 1
                sol = new_sol
                value = new_value

    print(
        f"Gen #{generation}: temp = {temp:.6f}, "
        f"best score = {best_score:.8f}, "
        f"cur score = {value:.8f}, "
        f"worse accepted = {round(accepted_worse/total_worse*100,2):.2f}%"
    )
    temp = temp * alpha
    


In [ ]:
best_sol

In [ ]:
score(2.0020773811812647, 0.2819354884901672, 0.050000764463366584)

In [ ]:
score(*best_sol)

In [ ]:
sol = best_sol
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))